# Test bed

In a console run: 

$ docker run -p 127.0.0.1:9042:9042 -i -t scylladb/scylla

or: 

$ docker run -p 127.0.0.1:9042:9042 -d cassandra

# Init

In [151]:
from cassandra.cluster import Cluster
from cassandra.util import uuid_from_time
from datetime import datetime

In [152]:
cluster = Cluster(['127.0.0.1'], port=9042, protocol_version=3)

In [153]:
session = cluster.connect()

In [154]:
cluster.metadata.cluster_name


u'Test Cluster'

In [155]:
cluster.metadata.all_hosts()

[<Host: 127.0.0.1 datacenter1>]

In [169]:
session.execute("DROP KEYSPACE glances")

In [170]:
session.execute("CREATE KEYSPACE glances WITH replication = { 'class': 'SimpleStrategy', 'replication_factor': '2' }")

In [171]:
session.set_keyspace('glances')

In [127]:
# Works with Scylla but not Cassandra...
#keyspaces = session.execute("SELECT * FROM system.schema_keyspaces")
#[k.keyspace_name for k in keyspaces]

# First data model

In [94]:
session.execute("CREATE TABLE cpu (hostname text, time timeuuid, stat map<text,float>, PRIMARY KEY (hostname, time))")

OperationTimedOut: errors={'127.0.0.1': 'Client request timeout. See Session.execute[_async](timeout)'}, last_host=127.0.0.1

In [79]:
tuuid = uuid_from_time(datetime.now())

In [39]:
session.execute(
    """
    INSERT INTO cpu (hostname, time, stat)
    VALUES (%s, %s, %s)
    """,
    ("localhost", tuuid, {"user": 30, "system": 31})
)

In [40]:
res = session.execute(
    """
    SELECT * FROM cpu
    """
)
for r in res:
    print(r)

Row(hostname=u'localhost', time=UUID('124732f4-2d88-11e6-9094-0826e0b87285'), stat=OrderedMapSerializedKey([(u'system', u'31'), (u'user', u'30')]))


In [44]:
r.stat['user']

u'30'

# Second data model

In [159]:
session.execute("CREATE TABLE localhost (plugin text, time timeuuid, stat map<text,float>, PRIMARY KEY (plugin, time)) WITH CLUSTERING ORDER BY (time DESC)")

In [160]:
tuuid = uuid_from_time(datetime.now())

In [167]:
session.execute(
    """
    INSERT INTO localhost (plugin, time, stat)
    VALUES (%s, %s, %s)
    """,
    ("cpu", tuuid, {"user": 30, "system": 30})
)

In [174]:
res = session.execute(
    """
    SELECT * FROM localhost
    """
)
for r in res:
    print(r)

Row(plugin=u'load', time=UUID('85d26c10-2f19-11e6-8e98-d693ce10ba5b'), stat=OrderedMapSerializedKey([(u'cpucore', 4.0), (u'history_size', 28800.0), (u'load_careful', 0.699999988079071), (u'load_critical', 5.0), (u'load_warning', 1.0), (u'min1', 0.15000000596046448), (u'min15', 0.15000000596046448), (u'min5', 0.14000000059604645)]))
Row(plugin=u'load', time=UUID('83ed6eea-2f19-11e6-9142-6befd54c51d7'), stat=OrderedMapSerializedKey([(u'cpucore', 4.0), (u'history_size', 28800.0), (u'load_careful', 0.699999988079071), (u'load_critical', 5.0), (u'load_warning', 1.0), (u'min1', 0.15000000596046448), (u'min15', 0.15000000596046448), (u'min5', 0.14000000059604645)]))
Row(plugin=u'load', time=UUID('82082c14-2f19-11e6-88bc-ce03ef6e0e16'), stat=OrderedMapSerializedKey([(u'cpucore', 4.0), (u'history_size', 28800.0), (u'load_careful', 0.699999988079071), (u'load_critical', 5.0), (u'load_warning', 1.0), (u'min1', 0.17000000178813934), (u'min15', 0.15000000596046448), (u'min5', 0.15000000596046448)])

In [101]:
session.shutdown()
cluster.shutdown()